# Synthetic Test
Given a synthetic signal called 'my_data', the folder `custom_data` should contain two files:
1. `custom_data/my_data.csv` for the timeseries
2. `custom_data/my_data_truth.csv` for the anomalies.

The following example showcases `my_data = synthetic_5`

In [24]:
from time import time
from tqdm import tqdm 
import site
import sys
import pandas as pd 
import numpy as np
import ast 
import matplotlib.pyplot as plt
import glob
import ast

site.addsitedir('Orion/')
site.addsitedir('MLPrimitives/')
site.addsitedir('mSSA/')


from orion.benchmark import benchmark, _summarize_results_datasets
from Orion.orion.evaluation import CONTEXTUAL_METRICS as METRICS
from Orion.orion.evaluation import contextual_confusion_matrix
from functools import partial


def _summarize_results_datasets_har(df):
    """ Summarize the result of benchmark.

    The table is summarized for  the number of anomalies detected, and
    the average f1 score acheived by that pipeline across datasets.
    """
    def return_cm(x):
        if isinstance(x, int):
            return (0, 0, 0)

        elif len(x) > 3:
            return x[1:]

        return x

#     def get_status(x):
#         return {
#             "OK": 0,
#             "ERROR": 1
#         }[x]

#     df['status'] = df['status'].apply(get_status)
    df['confusion_matrix'] = [str(x) for x in df['confusion_matrix'] ]
    df['confusion_matrix'] = df['confusion_matrix'].apply(ast.literal_eval)
    df['confusion_matrix'] = df['confusion_matrix'].apply(return_cm)
    df[['fp', 'fn', 'tp']] = pd.DataFrame(df['confusion_matrix'].tolist(), index=df.index)

    # calculate f1 score
    df_ = df.groupby(['dataset', 'pipeline','category','harmonics'])[['fp', 'fn', 'tp']].sum().reset_index()

    precision = df_['tp'] / (df_['tp'] + df_['fp'])
    recall = df_['tp'] / (df_['tp'] + df_['fn'])
    df_['f1'] = 2 * (precision * recall) / (precision + recall + 1e-10)
    return df_

def _summarize_results_datasets_category(df):
    """ Summarize the result of benchmark.

    The table is summarized for  the number of anomalies detected, and
    the average f1 score acheived by that pipeline across datasets.
    """
    def return_cm(x):
        if isinstance(x, int):
            return (0, 0, 0)

        elif len(x) > 3:
            return x[1:]

        return x

    def get_status(x):
        return {
            "OK": 0,
            "ERROR": 1
        }[x]

    df['status'] = df['status'].apply(get_status)
    df['confusion_matrix'] = [str(x) for x in df['confusion_matrix'] ]
    df['confusion_matrix'] = df['confusion_matrix'].apply(ast.literal_eval)
    df['confusion_matrix'] = df['confusion_matrix'].apply(return_cm)
    df[['fp', 'fn', 'tp']] = pd.DataFrame(df['confusion_matrix'].tolist(), index=df.index)

    # calculate f1 score
    df_ = df.groupby(['dataset', 'pipeline','category'])[['fp', 'fn', 'tp']].sum().reset_index()

    precision = df_['tp'] / (df_['tp'] + df_['fp'])
    recall = df_['tp'] / (df_['tp'] + df_['fn'])
    df_['f1'] = 2 * (precision * recall) / (precision + recall + 1e-10)
    return df_


In [16]:
if ('accuracy' in METRICS): del METRICS['accuracy']
METRICS['confusion_matrix'] = contextual_confusion_matrix
metrics = {k: partial(fun, weighted=False) for k, fun in METRICS.items()}

def make_hyperparams(datasets, rank):
    hyperparams = {}
    rank_dict = {"mssa": {"orion.primitives.mssa.mSSATAD#1": {"rank": rank}}}
    for k in datasets:
        hyperparams[k] = rank_dict
    return hyperparams




In [33]:

files = glob.glob('custom_data/**[0-9]_[0-9].csv')
datanames = [file.split('/')[1][:-4] for file in files]
score_dataframes = []
summary_dataframes = []
summary_dataframes_h = []
ranks = [None] + list(range(1,20))
datasets = {
    'custom': datanames
}

for rank in ranks:
    print(rank)
    pipelines = ['mssa']
    data = datasets
    for k, v in data.items():
        print(len(v))
    print(data)
    hyperparameters = make_hyperparams(data, rank)
    scores = benchmark(pipelines=pipelines, datasets=data, metrics=metrics, rank='f1', hyperparameters=hyperparameters, detrend=True)
    scores['rank'] = rank
    score_dataframes.append(scores)
    scores['confusion_matrix'] = [str(x) for x in scores['confusion_matrix']]
    scores['category'] = scores.signal.str.split('_').str[1]
    scores['harmonics'] = scores.signal.str.split('_').str[2]
    
    score_summary_c = _summarize_results_datasets_category(scores)
    score_summary_c['rank'] = rank
    summary_dataframes.append(score_summary_c)
    
    score_summary_h = _summarize_results_datasets_har(scores)
    score_summary_h['rank'] = rank
    summary_dataframes_h.append(score_summary_h)


pd.concat(score_dataframes, ignore_index=True).to_pickle("mssa_synthetic_scores.pkl")
pd.concat(summary_dataframes, ignore_index=True).to_pickle("mssa_synthetic_summaries.pkl")
pd.concat(summary_dataframes_h, ignore_index=True).to_pickle("mssa_synthetic_summaries_h.pkl")

Starting dataset custom with 281 signals..
HYPERPARAMS {'orion.primitives.mssa.mSSATAD#1': {'rank': None}}
Scoring pipeline mssa on signal synthetic_highrank_h11_2 (test split: False)
Scoring pipeline mssa on signal synthetic_highrank_h4_6 (test split: False)


None
281
{'custom': ['synthetic_highrank_h11_2', 'synthetic_highrank_h4_6', 'synthetic_lowrank_h14_6', 'synthetic_lowrank_h1_1', 'synthetic_highrank_h13_0', 'synthetic_highrank_h6_4', 'synthetic_lowrank_h3_3', 'synthetic_lowrank_h5_5', 'synthetic_lowrank_h10_2', 'synthetic_lowrank_h9_8', 'synthetic_highrank_h2_0', 'synthetic_lowrank_h12_0', 'synthetic_lowrank_h7_7', 'synthetic_lowrank_h7_6', 'synthetic_lowrank_h12_1', 'synthetic_highrank_h2_1', 'synthetic_lowrank_h9_9', 'synthetic_lowrank_h10_3', 'synthetic_lowrank_h5_4', 'synthetic_lowrank_h3_2', 'synthetic_highrank_h6_5', 'synthetic_highrank_h13_1', 'synthetic_lowrank_h1_0', 'synthetic_lowrank_h14_7', 'synthetic_highrank_h4_7', 'synthetic_highrank_h11_3', 'synthetic_highrank_h11_1', 'synthetic_highrank_h4_5', 'synthetic_lowrank_h14_5', 'synthetic_lowrank_h1_2', 'synthetic_highrank_h8_8', 'synthetic_highrank_h13_3', 'synthetic_highrank_h6_7', 'synthetic_lowrank_h3_0', 'synthetic_lowrank_h5_6', 'synthetic_lowrank_h10_1', 'synthetic_hig

Scoring pipeline mssa on signal synthetic_lowrank_h14_6 (test split: False)


      timestamp     value
0             1 -0.073788
1             2 -0.118845
2             3  0.061635
3             4  0.038031
4             5  0.336268
...         ...       ...
2495       2496  0.130441
2496       2497  0.360522
2497       2498 -0.191155
2498       2499 -0.010236
2499       2500  0.037353

[2500 rows x 2 columns]
TEST:        timestamp     value
0             1 -0.073788
1             2 -0.118845
2             3  0.061635
3             4  0.038031
4             5  0.336268
...         ...       ...
2495       2496  0.130441
2496       2497  0.360522
2497       2498 -0.191155
2498       2499 -0.010236
2499       2500  0.037353

[2500 rows x 2 columns]
no split
no split
TRUTH
   start   end
0   1162  1163
1   1204  1205
ANOMS
Empty DataFrame
Columns: [start, end, score]
Index: []
SCORES:  {'f1': 0.0, 'recall': 0.0, 'precision': 0.0, 'confusion_matrix': (None, 0, 2, 0), 'status': 'OK'}
MSSA RANK: 1
MSSA RANK: None
TRAIN:        timestamp     value
0             1 -0.

Scoring pipeline mssa on signal synthetic_lowrank_h1_1 (test split: False)
Scoring pipeline mssa on signal synthetic_highrank_h13_0 (test split: False)


...

TRUTH
Empty DataFrame
Columns: [start, end]
Index: []
ANOMS
   start  end     score
0    201  301  0.686265
SCORES:  {'f1': 0.0, 'recall': 0.0, 'precision': 0.0, 'confusion_matrix': (None, 1, 0, 0), 'status': 'OK'}
MSSA RANK: 1
MSSA RANK: 19
TRAIN:        timestamp     value
0             1 -0.102179
1             2  0.094650
2             3  0.128541
3             4  0.814453
4             5  1.022175
...         ...       ...
2495       2496  0.856259
2496       2497  0.393949
2497       2498  0.106217
2498       2499 -0.199058
2499       2500 -0.251032

[2500 rows x 2 columns]
TEST:        timestamp     value
0             1 -0.102179
1             2  0.094650
2             3  0.128541
3             4  0.814453
4             5  1.022175
...         ...       ...
2495       2496  0.856259
2496       2497  0.393949
2497       2498  0.106217
2498       2499 -0.199058
2499       2500 -0.251032

[2500 rows x 2 columns]
no split
no split
TRUTH
   start   end
0    953   954
1   1354  1355


Scoring pipeline mssa on signal synthetic_lowrank_h9_5 (test split: False)
Scoring pipeline mssa on signal synthetic_lowrank_h5_8 (test split: False)


TRUTH
   start   end
0   1205  1206
1   1694  1695
2   1880  1881
3   1887  1888
4   2220  2221
ANOMS
Empty DataFrame
Columns: [start, end, score]
Index: []
SCORES:  {'f1': 0.0, 'recall': 0.0, 'precision': 0.0, 'confusion_matrix': (None, 0, 5, 0), 'status': 'OK'}
MSSA RANK: 1
MSSA RANK: 19
TRAIN:        timestamp     value
0             1 -0.385897
1             2  0.168060
2             3  0.321555
3             4  0.296117
4             5  0.406193
...         ...       ...
2495       2496 -0.104445
2496       2497 -1.364760
2497       2498 -1.884667
2498       2499 -2.738837
2499       2500 -2.581983

[2500 rows x 2 columns]
TEST:        timestamp     value
0             1 -0.385897
1             2  0.168060
2             3  0.321555
3             4  0.296117
4             5  0.406193
...         ...       ...
2495       2496 -0.104445
2496       2497 -1.364760
2497       2498 -1.884667
2498       2499 -2.738837
2499       2500 -2.581983

[2500 rows x 2 columns]
no split
no split
TR

Scoring pipeline mssa on signal synthetic_highrank_h6_9 (test split: False)
Scoring pipeline mssa on signal synthetic_highrank_h8_6 (test split: False)


TRUTH
   start   end
0    121   122
1    520   521
2   1192  1193
3   2194  2195
4   2301  2302
5   2345  2346
ANOMS
   start   end     score
0    956  1137  0.389325
SCORES:  {'f1': 0.0, 'recall': 0.0, 'precision': 0.0, 'confusion_matrix': (None, 1, 6, 0), 'status': 'OK'}
MSSA RANK: 1
MSSA RANK: 19
TRAIN:        timestamp     value
0             1 -0.194974
1             2  0.104546
2             3  0.171872
3             4 -0.014957
4             5  0.169123
...         ...       ...
2495       2496 -0.199546
2496       2497 -0.139416
2497       2498 -0.178471
2498       2499 -0.393415
2499       2500 -0.191641

[2500 rows x 2 columns]
TEST:        timestamp     value
0             1 -0.194974
1             2  0.104546
2             3  0.171872
3             4 -0.014957
4             5  0.169123
...         ...       ...
2495       2496 -0.199546
2496       2497 -0.139416
2497       2498 -0.178471
2498       2499 -0.393415
2499       2500 -0.191641

[2500 rows x 2 columns]
no split
n

In [35]:
scores = pd.read_pickle('mssa_synthetic_scores.pkl')
summaries = pd.read_pickle('mssa_synthetic_summaries.pkl')
summaries_h = pd.read_pickle('mssa_synthetic_summaries_h.pkl')

In [40]:
summaries_h.loc[summaries_h.harmonics == 'h9']

dataset pipeline  category harmonics  fp  fn  tp        f1  rank
14   custom     mssa  highrank        h9   4  28   1  0.058824  None
28   custom     mssa   lowrank        h9   5  16  15  0.588235  None
43   custom     mssa  highrank        h9   5  29   0  0.000000     1
57   custom     mssa   lowrank        h9   2  29   2  0.114286     1
72   custom     mssa  highrank        h9   5  28   1  0.057143     2
86   custom     mssa   lowrank        h9  10  30   1  0.047619     2
101  custom     mssa  highrank        h9   6  27   2  0.108108     3
115  custom     mssa   lowrank        h9  14  26   5  0.200000     3
130  custom     mssa  highrank        h9   4  29   0  0.000000     4
144  custom     mssa   lowrank        h9  25  18  13  0.376812     4
159  custom     mssa  highrank        h9   7  28   1  0.054054     5
173  custom     mssa   lowrank        h9  15  12  19  0.584615     5
188  custom     mssa  highrank        h9  10  26   3  0.142857     6
202  custom     mssa   lowrank        h9   6  15  16  0.603774     6
217  custom     mssa  highrank        h9   5  29   0  0.000000     7
231  custom     mssa   lowrank        h9   5  23   8  0.363636     7
246  custom     mssa  highrank        h9   6  28   1  0.055556     8
260  custom     mssa   lowrank        h9   4  27   4  0.205128     8
275  custom     mssa  highrank        h9   4  29   0  0.000000     9
289  custom     mssa   lowrank        h9   2  30   1  0.058824     9
304  custom     mssa  highrank        h9   7  29   0  0.000000    10
318  custom     mssa   lowrank        h9   1  31   0  0.000000    10
333  custom     mssa  highrank        h9  12  27   2  0.093023    11
347  custom     mssa   lowrank        h9   5  30   1  0.054054    11
362  custom     mssa  highrank        h9   7  29   0  0.000000    12
376  custom     mssa   lowrank        h9   3  28   3  0.162162    12
391  custom     mssa  highrank        h9   7  28   1  0.054054    13
405  custom     mssa   lowrank        h9   4  30   1  0.055556    13
420  custom     mssa  highrank        h9   5  29   0  0.000000    14
434  custom     mssa   lowrank        h9   5  30   1  0.054054    14
449  custom     mssa  highrank        h9   5  29   0  0.000000    15
463  custom     mssa   lowrank        h9   3  30   1  0.057143    15
478  custom     mssa  highrank        h9  12  28   1  0.047619    16
492  custom     mssa   lowrank        h9  12  29   2  0.088889    16
507  custom     mssa  highrank        h9   7  29   0  0.000000    17
521  custom     mssa   lowrank        h9   9  29   2  0.095238    17
536  custom     mssa  highrank        h9   7  28   1  0.054054    18
550  custom     mssa   lowrank        h9   7  28   3  0.146341    18
565  custom     mssa  highrank        h9   7  27   2  0.105263    19
579  custom     mssa   lowrank        h9   5  31   0  0.000000    19

In [11]:
scores

pipeline  rank   f1  recall  precision confusion_matrix  status  \
0        mssa  None  1.0     1.0        1.0        (0, 0, 5)       0   
1        mssa  None  1.0     1.0        1.0        (0, 0, 4)       0   
2        mssa  None  1.0     1.0        1.0        (0, 0, 3)       0   
3        mssa  None  1.0     1.0        1.0        (0, 0, 3)       0   
4        mssa  None  1.0     1.0        1.0        (0, 0, 2)       0   
...       ...   ...  ...     ...        ...              ...     ...   
2805     mssa     9  0.0     0.0        0.0        (0, 5, 0)       0   
2806     mssa     9  0.0     0.0        0.0        (1, 2, 0)       0   
2807     mssa     9  0.0     0.0        0.0        (2, 5, 0)       0   
2808     mssa     9  0.0     0.0        0.0        (0, 5, 0)       0   
2809     mssa     9  0.0     0.0        0.0        (0, 5, 0)       0   

       elapsed  split dataset                    signal  category  fp  fn  tp  
0     0.069581  False  custom   synthetic_lowrank_h13_8   lowrank   0   0   5  
1     0.068907  False  custom    synthetic_lowrank_h8_3   lowrank   0   0   4  
2     0.075247  False  custom    synthetic_lowrank_h7_4   lowrank   0   0   3  
3     0.064005  False  custom    synthetic_lowrank_h7_8   lowrank   0   0   3  
4     0.130857  False  custom    synthetic_lowrank_h7_6   lowrank   0   0   2  
...        ...    ...     ...                       ...       ...  ..  ..  ..  
2805  0.072082  False  custom   synthetic_lowrank_h11_1   lowrank   0   5   0  
2806  0.073045  False  custom   synthetic_highrank_h9_8  highrank   1   2   0  
2807  0.121254  False  custom  synthetic_highrank_h12_3  highrank   2   5   0  
2808  0.081816  False  custom   synthetic_highrank_h7_7  highrank   0   5   0  
2809  0.080008  False  custom   synthetic_highrank_h8_6  highrank   0   5   0  

[2810 rows x 15 columns]